In [2]:
import geopandas as gpd

import pandas as pd
import altair as alt

### lese Bundesstraßen und Autobahnen

In [7]:
a_data= pd.read_csv(r"2016_A_S\2016_A_S.txt", sep=';', dtype={'Strnum': 'str'})#,nrows=1000000)


In [8]:
b_data= pd.read_csv(r"2016_B_S\2016_B_S.txt", sep=';', dtype={'Strnum': 'str'})#,nrows=1000000)


In [9]:
data = a_data.append(b_data, ignore_index=True)

In [10]:
len(data)

13703040

In [11]:
data.head()

TKNR   Zst  Land Strklas Strnum   Datum  Wotag Fahrtzw  Stunde  KFZ_R1  \
0  5329  4382    16       A     73  160101      5       s       1      16   
1  5329  4382    16       A     73  160101      5       s       2      32   
2  5329  4382    16       A     73  160101      5       s       3      17   
3  5329  4382    16       A     73  160101      5       s       4      11   
4  5329  4382    16       A     73  160101      5       s       5      16   

   ... Bus_R2  K_Bus_R2 LoA_R2  K_LoA_R2 Lzg_R2  K_Lzg_R2 Sat_R2  K_Sat_R2  \
0  ...      0         -      0         -      0         -      0         -   
1  ...      0         -      1         -      0         -      0         -   
2  ...      0         -      2         -      0         -      0         -   
3  ...      0         -      4         -      0         -      0         -   
4  ...      0         -      3         -      0         -      0         -   

  Son_R2  K_Son_R2  
0      0         -  
1      2         -  
2      3         -  
3      0         -  
4      0         -  

[5 rows x 57 columns]

In [12]:
data.Stunde=data.Stunde.apply(lambda x: 0 if x==24 else x)

data['datetime']=pd.to_datetime(( ("20" + data['Datum'].astype(str)) + '.'+ ("0" + data['Stunde'].astype(str)).str[-2:]  ), format='%Y%m%d.%H')

data['KFZ_ges']=data['KFZ_R1']+data['KFZ_R2']

data['weekday_name']=data.datetime.dt.weekday_name

data_fil=data[['Land','Strklas','datetime','weekday_name','KFZ_ges','Stunde']].copy()

---

### nach Bundesland

In [54]:
dict_bland= {
'1': 'Schleswig-Holstein',
'2': 'Hamburg',
'3': 'Niedersachsen',
'4': 'Bremen',
'5': 'Nordrhein-Westfalen',
'6': 'Hessen',
'7': 'Rheinland-Pfalz',
'8': 'Baden-Württemberg',
'9': 'Bayern',
'10': 'Saarland',
'11': 'Berlin',
'12': 'Brandenburg',
'13': 'Mecklenburg-Vorpommern',
'14': 'Sachsen',
'15': 'Sachsen-Anhalt',
'16': 'Thüringen'}

### Häufigkeit je Bundesland je Strassenklasse

In [24]:
dict_bland_freq_a=data.drop_duplicates('Zst')[data.Strklas=='A'].groupby('Land')['Zst'].size().to_dict()
dict_bland_freq_a

C:\Users\Simon\Anaconda3\envs\geo_julab\lib\site-packages\ipykernel_launcher.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  """Entry point for launching an IPython kernel.


{1: 21,
 3: 57,
 4: 5,
 5: 147,
 6: 62,
 7: 93,
 8: 34,
 9: 229,
 10: 55,
 11: 11,
 12: 14,
 13: 15,
 14: 33,
 15: 29,
 16: 23}

In [25]:
dict_bland_freq_b=data.drop_duplicates('Zst')[data.Strklas=='B'].groupby('Land')['Zst'].size().to_dict()
dict_bland_freq_b

C:\Users\Simon\Anaconda3\envs\geo_julab\lib\site-packages\ipykernel_launcher.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  """Entry point for launching an IPython kernel.


{1: 46,
 3: 73,
 4: 2,
 5: 109,
 6: 49,
 7: 71,
 8: 67,
 9: 73,
 10: 12,
 11: 6,
 12: 52,
 13: 51,
 14: 30,
 15: 55,
 16: 36}

In [26]:
data_group_land=data_fil.groupby(['weekday_name','Stunde','Land','Strklas'])['KFZ_ges'].mean()

data_group_land=data_group_land.reset_index().copy()


In [55]:
data_group_land['BLand'] = data_group_land.Land.apply(lambda x: dict_bland[str(x)])

In [27]:
#a_data_group_land['freq'] = a_data_group_land.Land 
data_group_land['freq_a'] = data_group_land.Land.apply(lambda x: dict_bland_freq_a[x])
data_group_land['freq_b'] = data_group_land.Land.apply(lambda x: dict_bland_freq_b[x])

In [56]:
data_group_land.to_csv('bast_2016_ab_grouped.csv', index=False)

In [32]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [99]:
data_group_land

weekday_name  Stunde  Land Strklas      KFZ_ges  freq_a  freq_b text  \
0          Friday       0     1       A   676.067385      21      46  bla   
1          Friday       0     1       B   167.896637      21      46  bla   
2          Friday       0     3       A  1059.468388      57      73  bla   
3          Friday       0     3       B   137.077281      57      73  bla   
4          Friday       0     4       A  1673.388679       5       2  bla   
...           ...     ...   ...     ...          ...     ...     ...  ...   
5035    Wednesday      23    14       B   135.137179      33      30  bla   
5036    Wednesday      23    15       A   991.895225      29      55  bla   
5037    Wednesday      23    15       B   118.246154      29      55  bla   
5038    Wednesday      23    16       A   723.411371      23      36  bla   
5039    Wednesday      23    16       B   130.063568      23      36  bla   

                   BLand  
0     Schleswig-Holstein  
1     Schleswig-Holstein  
2          Niedersachsen  
3          Niedersachsen  
4                 Bremen  
...                  ...  
5035             Sachsen  
5036      Sachsen-Anhalt  
5037      Sachsen-Anhalt  
5038           Thüringen  
5039           Thüringen  

[5040 rows x 9 columns]

In [154]:
source=data_group_land#.reset_index()#[df_group.year==2019]


selection = alt.selection_multi(fields=['BLand'], init=[{'BLand': 'Berlin'}])#,name="SelectorName"
selection2 = alt.selection_multi(fields=['weekday_name'])#, init={'weekday': 'Monday'})
selection3 = alt.selection_multi(fields=['Strklas'])#, init={'weekday': 'Monday'})


color_bland=alt.condition(
        selection,
        alt.value('gray'), 
        alt.value('lightgray'))

chart= alt.Chart(source).mark_line(point=True).encode(
    x='Stunde:O',
    #y='KFZ_ges:Q',
    y=alt.Y('KFZ_ges:Q', title='KFZ'),
    #color='weekday',
    color=alt.Color('weekday_name:N', legend=None),
    detail=['BLand','Strklas'],
    shape=alt.Shape('Strklas:O', legend=None),
    
    tooltip=[
        #alt.Tooltip('count(Land):Q', title='Messstation mit DTV'),
        #alt.Tooltip('freq', title='Anzahl Zählorte Bundesland'),
        alt.Tooltip('BLand', title='Bundesland')
        ],
    #row='year'
).transform_filter(
    selection
).transform_filter(
    selection2
).transform_filter(
    selection3
).interactive()

## interactive legend
legend_bland = alt.Chart(source).mark_rect(stroke='1',strokeOpacity=0.6,strokeWidth=0.2).encode(
        y=alt.Y('BLand:N', axis=alt.Axis(title='Bundesland', orient='right')),#,title='Bundesländer'),#  sort=["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]), , titleAnchor  ='start'
        color=color_bland,#alt.Color('Bundesland:N', legend=None),
        #tooltip=['count(Bundesland):Q'],#,'mean(cnt):Q']
        tooltip=[
            #alt.Tooltip('mean(KFZ_ges)', title='durchschnittl. KFZ pro h',format='.5'),
            alt.Tooltip('freq_a', title='Anzahl Zählorte Autobahn'),
            alt.Tooltip('freq_b', title='Anzahl Zählorte Bundesstr'),
#alt.Tooltip('count(Bundesland):Q', title='Messstation mit DTV'),
       # alt.Tooltip('Land', title='Bundesland')
        ],
    
    ).add_selection(
    selection
).properties(
        width=20,
    #title='Bundesland'
    )

## interactive legend
legend_weekday = alt.Chart(source).mark_point().encode(
    y=alt.Y('weekday_name:N', title='Wochentag', axis=alt.Axis(orient='right'), sort=["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]),
    #color=alt.Color('weekday_name:N', legend=None),
    color=alt.condition(selection2,
                    alt.Color('weekday_name:N', legend=None),
                    alt.value('lightgray')),
).add_selection(
    selection2
)

## interactive legend
legend_str = alt.Chart(source).mark_point().encode(
    y=alt.Y('Strklas:N', axis=alt.Axis(orient='right', titleX=65.), title='Straßenklasse'),
    #color=alt.Color('weekday_name:N', legend=None),
    color=alt.condition(selection3,
                    alt.value('black'),
                    alt.value('lightgray')),
        shape=alt.Shape('Strklas:O', legend=None),
).add_selection(
    selection3
)




full_ch=(chart | legend_bland | (legend_weekday & legend_str))

In [155]:
full_ch

alt.HConcatChart(...)

In [214]:
# adding Titel and Subtitle
title = alt.Chart(
    {"values": [{"text": "Tagesganglinien aus Bast-Zählstellen, 2016"}]}
).mark_text(size=20, align='left',strokeWidth=0,stroke='white').encode(  #,anchor='start' , align='left'
    text="text:N",
    x=alt.value(0)
)

subtitle = alt.Chart(
    {"values": [{"text": 'Quelle: https://www.bast.de/BASt_2017/DE/Verkehrstechnik/Fachthemen/v2-verkehrszaehlung/Stundenwerte.html'}]}
).mark_text(size=11, align='left').encode(
    text="text:N",
    x=alt.value(300),
    y=alt.value(50)
    #x=alt.value(100)
   # xOffset=-20
)
  
fullchart_title= alt.vconcat(
    title,
    full_ch,
    subtitle,#
).configure_view(
    stroke=None
).configure_concat(
    spacing=10
)

fullchart_title

alt.VConcatChart(...)

In [203]:
fullchart_title.save('bast_2016.html')

---

## Relative

In [229]:
data_group_land.head()

weekday_name  Stunde  Land Strklas      KFZ_ges  freq_a  freq_b text  \
0       Friday       0     1       A   676.067385      21      46  bla   
1       Friday       0     1       B   167.896637      21      46  bla   
2       Friday       0     3       A  1059.468388      57      73  bla   
3       Friday       0     3       B   137.077281      57      73  bla   
4       Friday       0     4       A  1673.388679       5       2  bla   

                BLand   KFZ_rel  
0  Schleswig-Holstein  0.201984  
1  Schleswig-Holstein  0.137751  
2       Niedersachsen  0.235869  
3       Niedersachsen  0.154607  
4              Bremen  0.202665

In [223]:
data_group_land.groupby(['BLand','Strklas'])['KFZ_ges'].max()

BLand                   Strklas
Baden-Württemberg       A          5303.911210
                        B          1863.913031
Bayern                  A          4964.363187
                        B          1260.535300
Berlin                  A          6783.868881
                        B          2044.721154
Brandenburg             A          4025.784367
                        B           721.746372
Bremen                  A          8256.905660
                        B          4120.846154
Hessen                  A          6103.837188
                        B          1285.375981
Mecklenburg-Vorpommern  A          2452.655346
                        B           861.510935
Niedersachsen           A          4491.771599
                        B           886.616438
Nordrhein-Westfalen     A          5761.612637
                        B          1083.780169
Rheinland-Pfalz         A          4315.413268
                        B          1885.291712
Saarland                A   

In [226]:
data_group_land['KFZ_rel']=data_group_land.KFZ_ges/data_group_land.groupby(['BLand','Strklas'])['KFZ_ges'].transform('max')

In [227]:
source=data_group_land#.reset_index()#[df_group.year==2019]


selection = alt.selection_multi(fields=['BLand'], init=[{'BLand': 'Berlin'}])#,name="SelectorName"
selection2 = alt.selection_multi(fields=['weekday_name'])#, init={'weekday': 'Monday'})
selection3 = alt.selection_multi(fields=['Strklas'])#, init={'weekday': 'Monday'})


color_bland=alt.condition(
        selection,
        alt.value('gray'), 
        alt.value('lightgray'))

chart= alt.Chart(source).mark_line(point=True).encode(
    x='Stunde:O',
    #y='KFZ_ges:Q',
    y=alt.Y('KFZ_rel:Q', title='KFZ_rel'),
    #color='weekday',
    color=alt.Color('weekday_name:N', legend=None),
    detail=['BLand','Strklas'],
    shape=alt.Shape('Strklas:O', legend=None),
    
    tooltip=[
        #alt.Tooltip('count(Land):Q', title='Messstation mit DTV'),
        #alt.Tooltip('freq', title='Anzahl Zählorte Bundesland'),
        alt.Tooltip('BLand', title='Bundesland')
        ],
    #row='year'
).transform_filter(
    selection
).transform_filter(
    selection2
).transform_filter(
    selection3
).interactive()

## interactive legend
legend_bland = alt.Chart(source).mark_rect(stroke='1',strokeOpacity=0.6,strokeWidth=0.2).encode(
        y=alt.Y('BLand:N', axis=alt.Axis(title='Bundesland', orient='right')),#,title='Bundesländer'),#  sort=["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]), , titleAnchor  ='start'
        color=color_bland,#alt.Color('Bundesland:N', legend=None),
        #tooltip=['count(Bundesland):Q'],#,'mean(cnt):Q']
        tooltip=[
            #alt.Tooltip('mean(KFZ_ges)', title='durchschnittl. KFZ pro h',format='.5'),
            alt.Tooltip('freq_a', title='Anzahl Zählorte Autobahn'),
            alt.Tooltip('freq_b', title='Anzahl Zählorte Bundesstr'),
#alt.Tooltip('count(Bundesland):Q', title='Messstation mit DTV'),
       # alt.Tooltip('Land', title='Bundesland')
        ],
    
    ).add_selection(
    selection
).properties(
        width=20,
    #title='Bundesland'
    )

## interactive legend
legend_weekday = alt.Chart(source).mark_point().encode(
    y=alt.Y('weekday_name:N', title='Wochentag', axis=alt.Axis(orient='right'), sort=["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]),
    #color=alt.Color('weekday_name:N', legend=None),
    color=alt.condition(selection2,
                    alt.Color('weekday_name:N', legend=None),
                    alt.value('lightgray')),
).add_selection(
    selection2
)

## interactive legend
legend_str = alt.Chart(source).mark_point().encode(
    y=alt.Y('Strklas:N', axis=alt.Axis(orient='right', titleX=65.), title='Straßenklasse'),
    #color=alt.Color('weekday_name:N', legend=None),
    color=alt.condition(selection3,
                    alt.value('black'),
                    alt.value('lightgray')),
        shape=alt.Shape('Strklas:O', legend=None),
).add_selection(
    selection3
)




full_ch=(chart | legend_bland | (legend_weekday & legend_str))

In [228]:
full_ch

alt.HConcatChart(...)

In [234]:
# adding Titel and Subtitle
title = alt.Chart(
    {"values": [{"text": "relative Tagesganglinien aus Bast-Zählstellen, 2016"}]}
).mark_text(size=20, align='left',strokeWidth=0,stroke='white').encode(  #,anchor='start' , align='left'
    text="text:N",
    x=alt.value(0)
)

subtitle = alt.Chart(
    {"values": [{"text": 'Anteil an Spitzenstunde pro Bundesland pro Straßenklasse'}]}
).mark_text(size=11, align='left').encode(
    text="text:N",
    x=alt.value(0),

    #x=alt.value(100)
   # xOffset=-20
)

quelle = alt.Chart(
    {"values": [{"text": 'Quelle: https://www.bast.de/BASt_2017/DE/Verkehrstechnik/Fachthemen/v2-verkehrszaehlung/Stundenwerte.html'}]}
).mark_text(size=11, align='left').encode(
    text="text:N",
    x=alt.value(330),
    y=alt.value(20)
    #x=alt.value(100)
   # xOffset=-20
)
  
fullchart_title= alt.vconcat(
    title,
    subtitle,
    full_ch,
    quelle,#
).configure_view(
    stroke=None
).configure_concat(
    spacing=10
)

fullchart_title

alt.VConcatChart(...)

In [235]:
fullchart_title.save('bast_2016_rel.html')